In [35]:
import numpy as np
import networkx as nx
import time
import math
import pandas as pd
import scipy as sp
import plotly.express as px
import plotly.graph_objs as go
from scipy.sparse import *
from scipy import linalg
from scipy.sparse.linalg import norm
from scipy.optimize import least_squares

Let's create two graphs from the list of edges downloaded from the Snap database. 

In [ ]:
G1 = nx.read_edgelist('../data/web-Stanford.txt', create_using=nx.DiGraph(), nodetype=int)

# G2 = nx.read_edgelist('../data/web-BerkStan.txt', create_using=nx.DiGraph(), nodetype=int)

### Creating the transition probability matrix

In [ ]:
# square matrix of size n x n, where n is the number of nodes in the graph. The matrix is filled with zeros and the (i,j) element is x if the node i is connected to the node j. Where x is 1/(number of nodes connected to i).

def create_matrix(G):
    n = G.number_of_nodes()
    P = sp.sparse.lil_matrix((n,n))
    for i in G.nodes():
        for j in G[i]: #G[i] is the list of nodes connected to i, it's neighbors
            P[i-1,j-1] = 1/len(G[i])
    return P

To ensure that the random process has a unique stationary distribution and it will not stagnate, the transition matrix P is usually modified to be an irreducible stochastic matrix A (called the Google matrix) as follows

$$ A = \alpha \tilde{P} + (1-\alpha)v e^T$$

Where $\tilde{P}$ is defined as 

$$ \tilde{P} = P + v d^T$$

Where $d \in \mathbb{N}^{n \times 1}$ s a binary vector tracing the indices of dangling web-pages with no hyperlinks, i.e., $d(i ) = 1$ if the `ith` page has no hyperlink, $v \in \mathbb{R}^{n \times 1}$ is a probability vector, $e = [1, 1, . . . , 1]^T$ , and $0 < \alpha < 1$ is the so-called damping factor that represents the probability in the model that the surfer transfer by clicking a hyperlink rather than other ways

In [ ]:
n = G1.number_of_nodes()
P = create_matrix(G1)    

the vector `d` solves the dangling nodes problem

In [ ]:
# define d as a nx1 sparse matrix, where n is the number of nodes in the graph. The vector is filled with d(i) = 1 if the i row of the matrix P is filled with zeros, other wise is 0

# d is the vector of dangling nodes
d = sp.sparse.lil_matrix((n,1))
for i in range(n):
    if P[i].sum() == 0:
        d[i] = 1

The vector v is a probability vector, the sum of its elements bust be one

In [ ]:
# define v as the probability vector of size n x 1, where n is the number of nodes in the graph. The vector is filled with 1/n
# https://en.wikipedia.org/wiki/Probability_vector

v = sp.sparse.lil_matrix((n,1))
for i in range(n):
    v[i] = 1/n  

Now we can compute the transition matrix


In [ ]:
Pt = P + v.dot(d.T)

# Pt is a sparse matrix too

In [ ]:
# e is a nx1 sparse matrix filled with ones
e = sp.sparse.lil_matrix((1,n))
for i in range(n):
    e[0,i] = 1

In [ ]:
# # v*eT is a nxn sparse matrix filled all with 1/n, let's call it B

# B = sp.sparse.lil_matrix((n,n))
# for i in range(n):
#     for j in range(n):
#         B[i,j] = 1/n

# A = alpha*Pt + (1-alpha)*B

## Algorithm 1 Shifted-Power method for PageRank with multiple damping factors:

In [ ]:
# pandas dataframe to store the results
df = pd.DataFrame(columns=['alpha', 'iterations', 'tau', 'time'])

In [ ]:
# this should return mv (the number of iteration needed for the convergence), and two vector called x and r. Where x is the vector of the pagerank and r is the residual vector

def Algorithm1(Pt, v, tau, max_mv, a: list):
    
    start_time = time.time()

    u = Pt.dot(v) - v 
    mv = 1 # number of matrix vector products
    r = sp.sparse.lil_matrix((n,1)) 
    Res = sp.sparse.lil_matrix((len(a),1))
    x = sp.sparse.lil_matrix((n,1))  

    for i in range(len(a)):
        r = a[i]*(u) 
        normed_r = norm(r)
        Res[i] = normed_r 

        if Res[i] > tau:
            x = r + v 

    while max(Res) > tau and mv < max_mv:
        u = Pt*u # should it be the same u of the beginning?
        mv += 1 

        for i in range(len(a)):
            if Res[i] >= tau: 
                r = (a[i]**(mv+1))*(u)
                Res[i] = norm(r)

                if Res[i] > tau:
                    x = r + x

    if mv == max_mv:
        print("The algorithm didn't converge in ", max_mv, " iterations")
    else:
        print("The algorithm converged in ", mv, " iterations")

    total_time = time.time() - start_time
    print("The algorithm took ", total_time, " seconds")
       
    return mv, x, r, total_time  

In [ ]:
# list of alpha values, from 0.85 to 0.99 with step 0.01
a = []
for i in range(85,100):
    a.append(i/100)

max_mv = 1000

# run the algorithm for different values of tau from 10^-5 to 10^-9 with step 10^-1
for i in range(5,10):
    tau = 10**(-i)
    print("\ntau = ", tau)
    mv, x, r, total_time = Algorithm1(Pt, v, tau, max_mv, a)
    df = df.append({'alpha': a, 'iterations': mv, 'tau': tau, 'time': total_time}, ignore_index=True) 



In [ ]:
# save the results in a csv file
df.to_csv('../data/results/algo1/different_tau.csv', index=False)

### Plotting the results of the algorithm for different values of tau, and fixed alpha

In [ ]:
x = df['tau'][::-1].tolist()
y = df['iterations'].tolist()

fig1 = go.Figure(data=go.Scatter(x=x, y=y, mode='lines+markers'), 
                                layout=go.Layout(title='Iterations needed for the convergence', xaxis_title='tau', yaxis_title='iterations'))
                                                                                
# save the plot in a html file
fig1.write_html("../data/results/algo1/taus_over_iterations.html")

##### RESULTS OVER TIME #####

x1 = df['tau'][::-1].tolist()
y1 = df['time'].tolist()

fig2 = go.Figure(data=go.Scatter(x=x1, y=y1, mode='lines+markers'),
                                layout=go.Layout(title='Time needed for the convergence', xaxis_title='tau', yaxis_title='time (seconds)'))

# save the plot in a html file
fig2.write_html("../data/results/algo1/taus_over_time.html")


To view the graph just use the command

```bash
firefox taus_over_iterations.html 
```
or 

```bash
firefox taus_over_time.html
```

_In the right folder_

In [30]:
def Arnoldi(A, v, m): #  defined ad algorithm 2 in the paper
    beta = norm(v)
    print("A")
    v = v/beta
    print("B")
    h = sp.sparse.lil_matrix((m,m))
    print("C")

    for j in range(m):
        w = A.dot(v)
        print("D")
        for i in range(j):
            h[i,j] = v.T.dot(w)
            print("E")
            w = w - h[i,j]*v[i]
            print("F")

        h[j+1,j] = norm(w)
        print("G")

        if h[j+1,j] == 0:
            print("The algorithm didn't converge")
            m = j
            v[m+1] = 0
            break
        else:
            print("H")
            v[j+1] = w**h[j+1,j]
            print("I")

    return v, h, m, beta, j

In [29]:
A = sp.sparse.rand(100,100, density=0.5, format='lil')
v = sp.sparse.rand(100,1, density=1, format='lil')
m = 100

In [ ]:
v, h, m, beta, j = Arnoldi(A, v, m)

In [ ]:
def Algo4(Pt, v, m, a: list, tau, maxit: int, x):
    
    iter = 1
    mv = 0
    e1 = sp.sparse.lil_matrix((1,n))
    e1[0,0] = 1
    x = sp.sparse.lil_matrix((len(a),1))
    I = sp.sparse.eye(n, n, format='lil')
    res = sp.sparse.lil_matrix((len(a),1))
    r = sp.sparse.lil_matrix((n,1))
    y = sp.sparse.lil_matrix((n,1))

    for i in range(len(a)):
        r = ((1-a[i])**a[i])*v - ((1**a[i])*I - Pt).dot(x)
        res[i] = a[i]*norm(r)

    def Find_k(res, maxit):
        k = 0
        for i in range(len(a)):
            if res[i] == max(res):
                k = i
                break
        return k

    def Find_gamma(res, a, k):
        gamma = sp.sparse.lil_matrix((len(a),1))
        for i in range(len(a)):
            if i != k:
                gamma[i] = (res[i]*a[k])/(res[k]*a[i])
            else:
                gamma[i] = 0
        return gamma


    while max(res) > tau and iter < maxit:
        k = Find_k(res, maxit)
        gamma = Find_gamma(res, a, k)
        v, h, m, beta, j = Arnoldi((1**a[k])*I - Pt, r, m)
        Hbar = sp.sparse.lil_matrix((m+1,m))
        Hbar[0:m,0:m] = h
        Hbar[m+1,0:m] = e1

        mv += j

        # solve the least squares problem for Hbar*x = beta*e1
        y = sp.sparse.linalg.least_squares(Hbar, beta*e1)
        res[k] = a[k]*norm(beta*e1 - Hbar*y)
        x[k] = x[k] + v*y[k]

        for i in range(len(a)):
            if i != k:
                if res[i] >= tau:
                    Hbar[i] = Hbar[k] + ((1-a[i])/a[i] - (1-a[k])/a[k])*I
                    z  = beta*e1 - Hbar*y
                    y = sp.sparse.linalg.solve(Hbar, gamma*beta*e1)
                    x = x + v*y
                    res[i] = a[i]**a[k]*gamma[i]*res[k]
        
        iter += 1
        
    return x, res, mv
